# Explaining ML Models trained with Tabular Data

Return to the [castle](https://github.com/Nkluge-correa/teeny-tiny_castle).

According to "_[The mythos of model interpretability](https://arxiv.org/pdf/1606.03490.pdf)_", these are the properties of an "_interpretable model_": 

> A human can repeat (_"simulatability"_) the computation process with a full understanding of the algorithm (_"algorithmic transparency"_) and every individual part of the model owns an intuitive explanation (_"decomposability"_).

Explainable AI (`XAI`) is an approach to artificial intelligence that aims to achieve this level of interpretability. In it, we seek to create transparent, interpretable models that can provide human-understandable explanations for their decisions or predictions.

The goal of `XAI` is to improve the trustworthiness and reliability of AI systems and facilitate collaboration between humans and machines. `XAI` techniques include methods for visualizing model internals, feature importance analysis, and rule extraction. 

By providing clear and interpretable explanations for the behavior of AI models, `XAI` can help to increase the transparency and accountability of these systems, which is particularly important in applications such as healthcare, finance, and law enforcement, where decisions made by AI models can have significant impacts on people's lives. 

![image](https://archive.org/serve/Black_Box_1987_Mulft_de_h_ASS/Black_Box_1987_Multisoft_de_h_ASS_screenshot.gif)

This notebook will explore several interpretability techniques that can be used (especially well) against shallow ML models (`break-down plots`, `interactive break-down plots`, `SHAP`, and  `LIME`). We will use the `German Scoring Dataset`, created by Professor Dr. Hans Hofmann. 

The data set has information about 1000 individuals, based on their classification as risky (bad = 0) or not (good = 1) credit applicants. We will not be using the full 21 features of the [original dataset](<https://archive.ics.uci.edu/ml/datasets/statlog+(german+credit+data)>), but a [reduced version](https://www.kaggle.com/datasets/kabure/german-credit-data-with-risk) with only 10 features + the target.

Below, we perform some simple pre-processing (e.g., substituting missing values for their `average value` or `mode`) to help the training of our model.

In [1]:
import numpy as np
import pandas as pd
seed = np.random.seed(666)

df = pd.read_csv(r'data/german_credit_data.csv')

for col in df.columns:
    if df[col].dtypes == 'object':
        df[col] = df[col].fillna(df[col].value_counts().index[0])
    elif df[col].dtypes == 'int64':
        df[col] = df[col].fillna(round(df[col].mean()))

display(df)

Age     Sex  Job Housing Saving accounts Checking account  Credit amount  \
0     67    male    2     own          little           little           1169   
1     22  female    2     own          little         moderate           5951   
2     49    male    1     own          little           little           2096   
3     45    male    2    free          little           little           7882   
4     53    male    2    free          little           little           4870   
..   ...     ...  ...     ...             ...              ...            ...   
995   31  female    1     own          little           little           1736   
996   40    male    3     own          little           little           3857   
997   38    male    2     own          little           little            804   
998   23    male    2    free          little           little           1845   
999   27    male    2     own        moderate         moderate           4576   

     Duration              Purpose  Risk  
0           6             radio/TV  good  
1          48             radio/TV   bad  
2          12            education  good  
3          42  furniture/equipment  good  
4          24                  car   bad  
..        ...                  ...   ...  
995        12  furniture/equipment  good  
996        30                  car  good  
997        12             radio/TV  good  
998        45             radio/TV   bad  
999        45                  car  good  

[1000 rows x 10 columns]

Now, we use the `LabelEncoder()` class to turn our labels into numerical values.

In [2]:
from sklearn.preprocessing import LabelEncoder

encoder = LabelEncoder()

df['Risk'] = encoder.fit_transform(df['Risk']) # good becomes 1, and becomes = 0

display(df)

Age     Sex  Job Housing Saving accounts Checking account  Credit amount  \
0     67    male    2     own          little           little           1169   
1     22  female    2     own          little         moderate           5951   
2     49    male    1     own          little           little           2096   
3     45    male    2    free          little           little           7882   
4     53    male    2    free          little           little           4870   
..   ...     ...  ...     ...             ...              ...            ...   
995   31  female    1     own          little           little           1736   
996   40    male    3     own          little           little           3857   
997   38    male    2     own          little           little            804   
998   23    male    2    free          little           little           1845   
999   27    male    2     own        moderate         moderate           4576   

     Duration              Purpose  Risk  
0           6             radio/TV     1  
1          48             radio/TV     0  
2          12            education     1  
3          42  furniture/equipment     1  
4          24                  car     0  
..        ...                  ...   ...  
995        12  furniture/equipment     1  
996        30                  car     1  
997        12             radio/TV     1  
998        45             radio/TV     0  
999        45                  car     1  

[1000 rows x 10 columns]

You can speed up the vizualization of your dataset by using tools like `ydata_profiling`.

[`ydata_profiling`](https://pypi.org/project/ydata-profiling/) generates profile reports from a pandas `DataFrame`. Extending a pandas `DataFrame` with `df.profile_report()`, will automatically generate a standardized univariate and multivariate report for data understanding.

In [3]:
from ydata_profiling import ProfileReport

profile = ProfileReport(df, title="Pandas Profiling Report")
profile.to_notebook_iframe()
profile.to_file("pandas_profiling_german_scoring.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Let us split the data set into `training` and `testing` groups, so we can later evaluate the performance of our models.


In [4]:
from sklearn.model_selection import train_test_split


X, y = df[df.columns.values.tolist()[0:9]], df[df.columns.values.tolist()[-1]]
X_train, X_test, y_train, y_test = train_test_split(
    X,
    y,
    test_size=0.2,
    random_state=seed
)

Below we are creating a `pipeline` to scale the numerical values to the same range (`StandardScaler()`) and one-hot-encode the categorial values into sparse binary vectors (`OneHotEncoder()`). For this, we are using some imported functions from the `Scikit-learn` library.


In [5]:
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import make_column_transformer
from sklearn.pipeline import make_pipeline

preprocess = make_column_transformer(
    (StandardScaler(), ['Age', 'Job', 'Credit amount', 'Duration']),
    (OneHotEncoder(), ['Sex', 'Housing', 'Saving accounts', 'Checking account', 'Purpose']))


Below we create a series of different models so that we can compare their performance and classifications later.

- Logistic Regression (LR): _LR is a statistical model that models the probability of one event (out of two alternatives) taking place by having the log-odds (the logarithm of the odds) for the event be a linear combination of one or more independent variables ("predictors"). To learn more, read "[Logistic regression and artificial neural network classification models: a methodology review](https://www.sciencedirect.com/science/article/pii/S1532046403000340)."_


In [6]:
from sklearn.linear_model import LogisticRegression

model_lr = make_pipeline(
    preprocess,
    LogisticRegression(penalty='l2'))
model_lr.fit(X_train, y_train.values.ravel())
score = model_lr.score(X_test, y_test.values.ravel())
print(f'Accuracy (Logistic Regression): ' +
      '{:.2f}'.format(score * 100) + ' %')


Accuracy (Logistic Regression): 72.50 %


- Random Forest (RF): _Random forests or random decision forests is an ensemble learning method for classification, regression, and other tasks that operates by constructing a multitude of decision trees at training time. For classification tasks, the output of the random forest is the class selected by most trees. To learn more, read "[A Random Forest Guided Tour](https://arxiv.org/abs/1511.05741)."_


In [7]:
from sklearn.ensemble import RandomForestClassifier

model_rf = make_pipeline(
    preprocess,
    RandomForestClassifier(max_depth=3, n_estimators=500))
model_rf.fit(X_train, y_train.values.ravel())
score = model_rf.score(X_test, y_test.values.ravel())
print(f'Accuracy (Random Forest): ' + '{:.2f}'.format(score * 100) + ' %')


Accuracy (Random Forest): 70.00 %


- Gradient Boosting (GB): _Gradient boosting is a machine learning technique used in regression and classification tasks, among others. It gives a prediction model in the form of an ensemble of weak prediction models, which are typically decision trees. To larn more, read "[Gradient boosting machines, a tutorial](https://www.frontiersin.org/articles/10.3389/fnbot.2013.00021/full)."_


In [8]:
from sklearn.ensemble import GradientBoostingClassifier

model_gbc = make_pipeline(
    preprocess,
    GradientBoostingClassifier(n_estimators=100))
model_gbc.fit(X_train, y_train.values.ravel())
score = model_gbc.score(X_test, y_test.values.ravel())
print(f'Accuracy (Gradient Boosting Classifier): ' +
      '{:.2f}'.format(score * 100) + ' %')


Accuracy (Gradient Boosting Classifier): 69.00 %


- Support-vector machine (SVM): _SVMs are supervised learning models with associated learning algorithms that analyze data for classification and regression analysis. SVM maps training examples to points in space to maximize the width of the gap between the two categories. To learn more, read "[A Tutorial on Support Vector Machines for Pattern Recognition](https://www.di.ens.fr/~mallat/papiers/svmtutorial.pdf)."_


In [9]:
from sklearn.svm import SVC

model_svm = make_pipeline(
    preprocess,
    SVC(probability=True))
model_svm.fit(X_train, y_train.values.ravel())
score = model_svm.score(X_test, y_test.values.ravel())
print(f'Accuracy (Support-vector machine): ' +
      '{:.2f}'.format(score * 100) + ' %')


Accuracy (Support-vector machine): 69.50 %


Now we compare the model's predictions by using two generated samples: `Bob` and `Charles`.

- Note: _to read the features of each sample, read the descriptions presented above._


In [10]:

sample_1 = pd.DataFrame({'Age': [23],
                         'Sex': ['male'],
                         'Job': [2],
                         'Housing': ['rent'],
                         'Saving accounts': ['little'],
                         'Checking account': ['little'],
                         'Credit amount': [10000],
                         'Duration': [45],
                         'Purpose': ['car'],
                         },
                        index=['Bob'])

sample_2 = pd.DataFrame({'Age': [45],
                         'Sex': ['male'],
                         'Job': [2],
                         'Housing': ['own'],
                         'Saving accounts': ['moderate'],
                         'Checking account': ['moderate'],
                         'Credit amount': [4000],
                         'Duration': [24],
                         'Purpose': ['repairs'],
                         },
                        index=['Charles'])


def what_does_the_models_think(df):
    sample = df
    if model_lr.predict_proba(sample)[0][0] > model_lr.predict_proba(sample)[0][1]:
        print(
            f'LR: {sample.index[0]} its not  credible...{round(model_lr.predict_proba(sample)[0][0] * 100, 2)} %')
    else:
        print(
            f'LR: {sample.index[0]} is credible! {round(model_lr.predict_proba(sample)[0][1] * 100, 2)} %')

    if model_rf.predict_proba(sample)[0][0] > model_rf.predict_proba(sample)[0][1]:
        print(
            f'RF: {sample.index[0]} its not  credible...{round(model_rf.predict_proba(sample)[0][0] * 100, 2)} %')
    else:
        print(
            f'RF: {sample.index[0]} is credible! {round(model_rf.predict_proba(sample)[0][1] * 100, 2)} %')

    if model_gbc.predict_proba(sample)[0][0] > model_gbc.predict_proba(sample)[0][1]:
        print(
            f'GB: {sample.index[0]} its not  credible...{round(model_gbc.predict_proba(sample)[0][0] * 100, 2)} %')
    else:
        print(
            f'GB: {sample.index[0]} is credible! {round(model_gbc.predict_proba(sample)[0][1] * 100, 2)} %')

    if model_svm.predict_proba(sample)[0][0] > model_svm.predict_proba(sample)[0][1]:
        print(
            f'SVM: {sample.index[0]} its not  credible...{round(model_svm.predict_proba(sample)[0][0] * 100, 2)} %')
    else:
        print(
            f'SVM: {sample.index[0]} is credible! {round(model_svm.predict_proba(sample)[0][1] * 100, 2)} %')


print(f'Predictions for {sample_1.index[0]}:\n')
what_does_the_models_think(sample_1)
print(f'\nPredictions for {sample_2.index[0]}:\n')
what_does_the_models_think(sample_2)


Predictions for Bob:

LR: Bob its not  credible...66.61 %
RF: Bob its not  credible...50.12 %
GB: Bob its not  credible...72.55 %
SVM: Bob its not  credible...77.73 %

Predictions for Charles:

LR: Charles is credible! 63.22 %
RF: Charles is credible! 69.56 %
GB: Charles is credible! 77.58 %
SVM: Charles is credible! 76.56 %


Above, you can see that different models (_trained with the same data-set_) can `output different classifications` for the same input sample. Let's try exploring the models that predicted different results for *Bob* and *Charles*.

---

## Creating Explainers with `Dalex`

[Dalex](https://pypi.org/project/dalex/) is a library for XAI (Explainable AI).

- We can create a wrapper around a predictive model using the' Explainer' object. Wrapped models may then be explored and compared with a collection of model-level and predict-level explanations.
- _As soon as the explainer object is created, you already receive `metadata` about the development of the wrapped model._

In [11]:
import dalex as dx

model_lr_exp = dx.Explainer(model_lr,
                            X, y, label='Logistic Regression explainer',
                            model_type='binary classification')


model_svm_exp = dx.Explainer(model_svm,
                             X, y, label='Support-vector machine explainer',
                             model_type='binary classification')


Preparation of a new explainer is initiated

  -> data              : 1000 rows 9 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarray.
  -> target variable   : 1000 values
  -> model_class       : sklearn.linear_model._logistic.LogisticRegression (default)
  -> label             : Logistic Regression explainer
  -> predict function  : <function yhat_proba_default at 0x00000264B0F7DCA0> will be used (default)
  -> predict function  : Accepts only pandas.DataFrame, numpy.ndarray causes problems.
  -> predicted values  : min = 0.175, mean = 0.702, max = 0.961
  -> model type        : binary classification will be used
  -> residual function : difference between y and yhat (default)
  -> residuals         : min = -0.931, mean = -0.00239, max = 0.767
  -> model_info        : package sklearn

A new explainer has been created!
Preparation of a new explainer is initiated

  -> data              : 1000 rows 9 cols
  -> target variable   : Parameter 'y' 

## Break-down plots (`BD`)

`BD` plots with variable attribution offer the decomposition of the model's prediction into contributions that can be attributed to different explanatory variables.

- Intuition : _Which variables contribute to this result the most?_

Source: _[Explaining Classifications for Individual Instances](https://doi.org/10.1109/tkde.2007.190734)_.


In [16]:
bd_sample_1 = model_lr_exp.predict_parts(sample_1,
                                         type='break_down')

bd_sample_1.result
fig = bd_sample_1.plot(show=False)
fig.update_layout(
    template='ggplot2',
    font_color='black')
fig.show()
fig.write_html('bob.html')

bd_sample_2 = model_lr_exp.predict_parts(sample_2,
                                         type='break_down')

bd_sample_2.result
fig = bd_sample_2.plot(show=False)
fig.update_layout(
    template='ggplot2',
    font_color='black')
fig.show()
#fig.to_html('charles.html')


### Limitations of `BD` plots

An important issue is that `BD` plots may be `misleading` for models including `interactions`.This is because the plots show only the `additive attributions`. Thus, the choice of the `ordering` of the explanatory variables that are used in the calculation of the variable-importance measures `is important. Also, for models with a large number of variables, `BD` plots may be complex and include many explanatory variables with small contributions to the instance prediction.

---

## Interactive Break-down plots (`iBD`)

Interaction (deviation from additivity) means that the effect of an explanatory variable depends on the value(s) of other variable(s). When we have interactions, the order in which variables are analyzed matters, and this can change the contribution score of a predictor (variable). However, some algorithms allow us to include interactions in `BD` plots.

Source: _[iBreakDown: Uncertainty of Model Explanations for Non-additive Predictive Models](https://arxiv.org/abs/1903.11420v1)_.

In [19]:

ibd_sample_1 = model_svm_exp.predict_parts(sample_1,
                                           type='break_down_interactions',
                                           interaction_preference=10)

ibd_sample_1.result


fig = ibd_sample_1.plot(show=False)
fig.update_layout(
    template='plotly_dark',
    title='Bob Classification (Support-vector machine)',
    paper_bgcolor='rgba(0, 0, 0, 0)',
    plot_bgcolor='rgba(0, 0, 0, 0)',
    font_color='white')
fig.show()


ibd_sample_2 = model_svm_exp.predict_parts(sample_2,
                                           type='break_down_interactions',
                                           interaction_preference=10)

ibd_sample_2.result


fig = ibd_sample_2.plot(show=False)
fig.update_layout(
    template='plotly_dark',
    title='Charles Classification (Support-vector machine)',
    paper_bgcolor='rgba(0, 0, 0, 0)',
    plot_bgcolor='rgba(0, 0, 0, 0)',
    font_color='white')
fig.show()


### Limitations of `iBD` plots

Though the numerical complexity of the `iBD` procedure is quadratic, it may be time-consuming in models with many explanatory variables. For a model with $p$ explanatory variables, we have got to calculate: 

$$p \times \frac{( p + 1 )}{2}$$

Net contributions for single variables and pairs of variables.

For datasets with a small number of observations, the calculations of the net contributions will be subject to a larger variability and, therefore, larger randomness in the ranking of the contributions.

---

## Shapley Additive Explanations (`SHAP`) for Average Attributions

`SHAP` values are another approach to address the ordering issue. It is based on the idea of averaging the value of a variable's attribution over all (or a large number of) possible orderings. The idea is closely linked to "_[Shapley values](https://en.wikipedia.org/wiki/Shapley_value)_".

Source: _[An Efficient Explanation of Individual Classifications Using Game Theory](http://dl.acm.org/citation.cfm?id=1756006.1756007)_.

In [22]:
shap_sample_1 = model_lr_exp.predict_parts(sample_1,
                                           type='shap')

shap_sample_1.result
fig = shap_sample_1.plot(show=False)
fig.update_layout(
    template='plotly_dark',
    title='Bob Classification (Logistic Regression)',
    paper_bgcolor='rgba(0, 0, 0, 0)',
    plot_bgcolor='rgba(0, 0, 0, 0)',
    font_color='white')
fig.show()

shap_sample_2 = model_lr_exp.predict_parts(sample_2,
                                           type='shap')

shap_sample_2.result
fig = shap_sample_2.plot(show=False)
fig.update_layout(
    template='plotly_dark',
    title='Charles Classification (Logistic Regression)',
    paper_bgcolor='rgba(0, 0, 0, 0)',
    plot_bgcolor='rgba(0, 0, 0, 0)',
    font_color='white')
fig.show()


### Limitations of `SHAP`

An important drawback of Shapley values is that they provide additive contributions (attributions) of explanatory variables. If the model is not additive, the Shapley values may be misleading. An important practical limitation of the general model-agnostic method is that, for large models, the calculation of Shapley values is time-consuming. However, sub-sampling can be used to address the issue (i.e., choosing a smaller collection of features to explore).

---

## Local Interpretable Model-agnostic Explanations (`LIME`)

The key idea behind this methodology is to locally approximate a black-box model by a simpler glass-box model, which is easier to interpret. The method has been widely adopted in text and image analysis, partly due to the interpretable data representation.

- Check our lime notebook [`lime_for_NLP`](https://github.com/Nkluge-correa/teeny-tiny_castle/blob/fa17764aa8800c388d0d298b750c686757e0861e/ML%20Explainability/NLP%20Interpreter/lime_for_NLP.ipynb) for an example of utilizing LIME with NLP models.
- Check our lime notebook [`lime_for_CV`](https://github.com/Nkluge-correa/teeny-tiny_castle/blob/fa17764aa8800c388d0d298b750c686757e0861e/ML%20Explainability/CV%20Interpreter/CNN_attribution_maps_with_LIME.ipynb) for an example of utilizing LIME with CV models.

Source: _["Why Should I Trust You?": Explaining the Predictions of Any Classifier](https://arxiv.org/abs/1602.04938?context=cs)_.

Note: _lime library requires categorical variables to be encoded in a numerical format._


In [ ]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()

X['Sex'] = le.fit_transform(X['Sex'])
X['Job'] = le.fit_transform(X['Job'])
X['Housing'] = le.fit_transform(X['Housing'])
X['Saving accounts'] = le.fit_transform(X['Saving accounts'])
X['Checking account'] = le.fit_transform(X['Checking account'])
X['Duration'] = le.fit_transform(X['Duration'])
X['Purpose'] = le.fit_transform(X['Purpose'])

model_lr_lime = LogisticRegression(penalty='l2')
model_lr_lime.fit(X.values, y)


Now, we create both of our samples (Bob and Charles).

In [20]:
Bob = pd.Series([23, 1, 2, 0, 0, 0, 10000, 24, 0],
                index=['Age', 'Sex', 'Job', 'Housing', 'Saving accounts',
                       'Checking account', 'Credit amount', 'Duration',
                       'Purpose'])
Charles = pd.Series([45, 1, 2, 2, 1, 1, 4000, 45, 4],
                    index=['Age', 'Sex', 'Job', 'Housing', 'Saving accounts',
                           'Checking account', 'Credit amount', 'Duration',
                                  'Purpose'])


And by using the `LimeTabularExplainer`, we can easily create an explainer for this classifier.

In [33]:
from IPython.display import display, HTML
from lime.lime_tabular import LimeTabularExplainer

explainer = LimeTabularExplainer(X,
                                 feature_names=X.columns,
                                 class_names=['bad', 'good'],
                                 discretize_continuous=False,
                                 verbose=True)

print("Bob's explainer:\n")

lime_exp_1 = explainer.explain_instance(Bob, model_lr_lime.predict_proba)

lime_exp_1.show_in_notebook(show_table=True)

#lime_exp_1.save_to_file('sample_1_explainer.html')

lime_exp_2 = explainer.explain_instance(Charles, model_lr_lime.predict_proba)

lime_exp_2.show_in_notebook(show_table=True)

#lime_exp_2.save_to_file('sample_1_explainer.html')

Bob's explainer:

Intercept 0.7033266679006458
Prediction_local [0.41635891]
Right: 0.3916309209235673


Intercept 0.7026586500121915
Prediction_local [0.46881387]
Right: 0.451214684719022


But you can also create your own graphical explanation using the features and attributions provided by the `explainer`.

In [35]:
features, attributions = zip(*lime_exp_1.as_list())

import matplotlib
import matplotlib.cm as cm
import matplotlib.colors as mcolors
from IPython.display import HTML

minima = min(attributions)
maxima = max(attributions)

norm = matplotlib.colors.Normalize(vmin=minima, vmax=maxima, clip=True)
mapper = cm.ScalarMappable(norm=norm, cmap=cm.YlOrRd)

colors = [mcolors.to_hex(mapper.to_rgba(v)) for v in attributions]

import plotly.graph_objects as go

fig = go.Figure(go.Bar(
        x=attributions,
        y=features,
        orientation='h',
        marker_color=colors))
fig.update_xaxes(ticksuffix = "",
                griddash='dash')

fig.update_layout(
    template='plotly_dark',
    title_text=f'Atributions and Features (Bob)',
    paper_bgcolor='rgba(0, 0, 0, 0)',
    plot_bgcolor='rgba(0, 0, 0, 0)')

fig.show()


### Limitations of `LIME`

There are several important limitations; for example, there have been various proposals for finding interpretable representations for continuous and categorical explanatory variables in the case of tabular data. The issue has not been solved yet. This leads to different implementations of `LIME`, which use different variable-transformation methods and can lead to different results.

Also, the method does not control the quality of the local fit of the glass-box model to the data. Thus, the latter model may be misleading. Also, defining a "_local neighborhood_" of the instance of interest may not be straightforward. Sometimes even slight changes in the neighborhood strongly affect the obtained explanations.

---

Return to the [castle](https://github.com/Nkluge-correa/teeny-tiny_castle).